In [1]:
# Import libraries
import IPython
import math
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import xgboost as xgb
import lightgbm as lgb
from sklearn.metrics import accuracy_score
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV,RandomizedSearchCV,StratifiedKFold
# Set up any configuration, options, or magic commands
%matplotlib inline

In [2]:
import warnings
warnings.filterwarnings('ignore')

In [3]:
# import os
# path = os.getcwd()
# path

In [4]:
df_mc = pd.read_csv("Dataset_without_outliers_both_class.csv")
df_mc.drop(['Unnamed: 0','binary_target'], axis=1)

baseline value  accelerations  fetal_movement  uterine_contractions  \
0              120.0          0.000           0.000                 0.000   
1              132.0          0.006           0.000                 0.006   
2              133.0          0.003           0.000                 0.008   
3              134.0          0.003           0.000                 0.008   
4              132.0          0.007           0.000                 0.008   
...              ...            ...             ...                   ...   
2121           140.0          0.000           0.000                 0.007   
2122           140.0          0.001           0.000                 0.007   
2123           140.0          0.001           0.000                 0.007   
2124           140.0          0.001           0.000                 0.006   
2125           142.0          0.002           0.002                 0.008   

      light_decelerations  severe_decelerations  prolongued_decelerations  \
0                   0.000                   0.0                       0.0   
1                   0.003                   0.0                       0.0   
2                   0.003                   0.0                       0.0   
3                   0.003                   0.0                       0.0   
4                   0.000                   0.0                       0.0   
...                   ...                   ...                       ...   
2121                0.000                   0.0                       0.0   
2122                0.000                   0.0                       0.0   
2123                0.000                   0.0                       0.0   
2124                0.000                   0.0                       0.0   
2125                0.000                   0.0                       0.0   

      abnormal_short_term_variability  mean_value_of_short_term_variability  \
0                                73.0                                   0.5   
1                                17.0                                   2.1   
2                                16.0                                   2.1   
3                                16.0                                   2.4   
4                                16.0                                   2.4   
...                               ...                                   ...   
2121                             79.0                                   0.2   
2122                             78.0                                   0.4   
2123                             79.0                                   0.4   
2124                             78.0                                   0.4   
2125                             74.0                                   0.4   

      percentage_of_time_with_abnormal_long_term_variability  ...  \
0                                                  27.5       ...   
1                                                   0.0       ...   
2                                                   0.0       ...   
3                                                   0.0       ...   
4                                                   0.0       ...   
...                                                 ...       ...   
2121                                               25.0       ...   
2122                                               22.0       ...   
2123                                               20.0       ...   
2124                                               27.0       ...   
2125                                               27.5       ...   

      histogram_min  histogram_max  histogram_number_of_peaks  \
0              62.0          126.0                        2.0   
1              68.0          198.0                        6.0   
2              68.0          198.0                        5.0   
3              53.0          170.0                       11.0   
4              53.0          170.0                   

In [312]:
df_mc_class1 = df_mc[df_mc.target==1]
df_mc_class2 = df_mc[df_mc.target==2]
df_mc_class3 = df_mc[df_mc.target==3]

In [313]:
df_mc_class1.shape, df_mc_class2.shape, df_mc_class3.shape

((1655, 24), (295, 24), (176, 24))

In [314]:
df_mc_class2_train = df_mc_class2.iloc[:155]
df_mc_class2_train = df_mc_class2_train.drop(['Unnamed: 0','binary_target'], axis=1)
df_mc_class2_train

baseline value  accelerations  fetal_movement  uterine_contractions  \
0             120.0          0.000          0.0000                 0.000   
10            151.0          0.000          0.0000                 0.001   
11            150.0          0.000          0.0000                 0.001   
17            131.0          0.002          0.0075                 0.003   
28            132.0          0.000          0.0075                 0.001   
..              ...            ...             ...                   ...   
445           142.0          0.000          0.0040                 0.000   
446           142.0          0.000          0.0060                 0.000   
447           142.0          0.000          0.0040                 0.000   
461           120.0          0.000          0.0020                 0.000   
465           144.0          0.000          0.0020                 0.001   

     light_decelerations  severe_decelerations  prolongued_decelerations  \
0                 0.0000                   0.0                       0.0   
10                0.0010                   0.0                       0.0   
11                0.0010                   0.0                       0.0   
17                0.0050                   0.0                       0.0   
28                0.0075                   0.0                       0.0   
..                   ...                   ...                       ...   
445               0.0000                   0.0                       0.0   
446               0.0000                   0.0                       0.0   
447               0.0000                   0.0                       0.0   
461               0.0000                   0.0                       0.0   
465               0.0010                   0.0                       0.0   

     abnormal_short_term_variability  mean_value_of_short_term_variability  \
0                               73.0                                   0.5   
10                              64.0                                   1.9   
11                              64.0                                   2.0   
17                              18.0                                   2.4   
28                              29.0                                   3.2   
..                               ...                                   ...   
445                             68.0                                   0.3   
446                             69.0                                   0.3   
447                             68.0                                   0.3   
461                             69.0                                   0.3   
465                             78.0                                   0.6   

     percentage_of_time_with_abnormal_long_term_variability  ...  \
0                                                 27.5       ...   
10                                                 9.0       ...   
11                                                 8.0       ...   
17                                                 0.0       ...   
28                                                 0.0       ...   
..                                                 ...       ...   
445                                               27.5       ...   
446                                               27.5       ...   
447                                               27.5       ...   
461                                               21.0       ...   
465                                               23.0       ...   

     histogram_min  histogram_max  histogram_number_of_peaks  \
0             62.0          126.0                        2.0   
10            56.0          186.0                        2.0   
11            56.0          186.0                        5.0   
17            67.0          174.0                        5.0   
28            50.0          191.0                        7.0   
..             ...            ...        

In [315]:
df_mc_class3_train = df_mc_class3.iloc[:100]
df_mc_class3_train = df_mc_class3_train.drop(['Unnamed: 0','binary_target'], axis=1)
df_mc_class3_train

baseline value  accelerations  fetal_movement  uterine_contractions  \
5              134.0          0.001           0.000                 0.010   
6              134.0          0.001           0.000                 0.013   
7              122.0          0.000           0.000                 0.000   
8              122.0          0.000           0.000                 0.002   
9              122.0          0.000           0.000                 0.003   
...              ...            ...             ...                   ...   
1708           131.0          0.000           0.003                 0.003   
1727           134.0          0.000           0.000                 0.009   
1749           134.0          0.002           0.002                 0.000   
1750           134.0          0.005           0.002                 0.002   
1751           134.0          0.004           0.001                 0.001   

      light_decelerations  severe_decelerations  prolongued_decelerations  \
5                  0.0075                   0.0                       0.0   
6                  0.0075                   0.0                       0.0   
7                  0.0000                   0.0                       0.0   
8                  0.0000                   0.0                       0.0   
9                  0.0000                   0.0                       0.0   
...                   ...                   ...                       ...   
1708               0.0075                   0.0                       0.0   
1727               0.0060                   0.0                       0.0   
1749               0.0020                   0.0                       0.0   
1750               0.0030                   0.0                       0.0   
1751               0.0040                   0.0                       0.0   

      abnormal_short_term_variability  mean_value_of_short_term_variability  \
5                                26.0                                   3.2   
6                                29.0                                   3.2   
7                                83.0                                   0.5   
8                                84.0                                   0.5   
9                                86.0                                   0.3   
...                               ...                                   ...   
1708                             67.0                                   1.7   
1727                             64.0                                   1.5   
1749                             63.0                                   1.5   
1750                             62.0                                   1.5   
1751                             60.0                                   1.6   

      percentage_of_time_with_abnormal_long_term_variability  ...  \
5                                                   0.0       ...   
6                                                   0.0       ...   
7                                                   6.0       ...   
8                                                   5.0       ...   
9                                                   6.0       ...   
...                                                 ...       ...   
1708                                                0.0       ...   
1727                                                0.0       ...   
1749                                                0.0       ...   
1750                                                0.0       ...   
1751                                                0.0       ...   

      histogram_min  histogram_max  histogram_number_of_peaks  \
5              50.0          200.0                        5.0   
6              50.0          200.0                        6.0   
7              62.0          130.0                        0.0   
8              62.0          130.0                        0.0   
9              62.0          130.0                   

In [562]:
def get_train_batch(target1, target2, target3, start, end):
    df_train = pd.concat([target1[start:end], target2, target3], axis=0)

    X_train = df_train.drop(['Unnamed: 0','target','binary_target'], axis=1)
    y_train = df_train.target
    return X_train, y_train 

In [563]:
X_train, y_train = get_train_batch(df_mc_class1, df_mc_class2_train, df_mc_class3_train, 0, 206)

In [564]:
y_train = y_train.map({1: 0, 2: 1, 3: 2})
y_train

1       0
2       0
3       0
4       0
12      0
       ..
1708    2
1727    2
1749    2
1750    2
1751    2
Name: target, Length: 461, dtype: int64

In [565]:
xgboost1 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost1 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [566]:
random_search.best_params_

{'reg_lambda': 1,
 'reg_alpha': 1e-05,
 'max_depth': 15,
 'learning_rate': 0.01,
 'gamma': 0.0,
 'colsample_bytree': 0.7}

In [567]:
xgboost1 = xgb.XGBClassifier(
reg_lambda = 1e-05,
reg_alpha = 1,
max_depth = 18,
learning_rate = 0.1,
gamma = 0.2,
colsample_bytree = 0.3
)
xgboost1.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.3, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.2, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=18, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              objective='multi:softprob', predictor=None, ...)

In [568]:
lgb1 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb1 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[CV 4/5] END colsample_bytree=0.9, gamma=0.1, learning_rate=0.001, max_depth=15, reg_alpha=10, reg_lambda=10;, score=0.898 total time=   0.1s
[CV 4/5] END colsample_bytree=0.9, gamma=0.2, learning_rate=0.01, max_depth=15, reg_alpha=0.1, reg_lambda=1;, score=0.880 total time=   0.1s
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Number of positive: 224, number of negative: 208
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002166 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 702
[LightGBM] [Info] Number of data points in the train se

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [569]:
random_search.best_params_

{'subsample': 1.0,
 'reg_lambda': 0.5,
 'reg_alpha': 0.5,
 'num_leaves': 31,
 'n_estimators': 50,
 'min_child_samples': 50,
 'max_depth': 10,
 'learning_rate': 0.05,
 'colsample_bytree': 1.0}

In [570]:
lgb1 = lgb.LGBMClassifier(
subsample = 0.6,
reg_lambda= 0.5,
reg_alpha =0.5,
num_leaves = 31,
n_estimators = 50,
min_child_samples = 20,
max_depth = 15,
learning_rate = 0.1,
colsample_bytree = 0.8
)
lgb1.fit(X_train,y_train)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000363 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 731
[LightGBM] [Info] Number of data points in the train set: 461, number of used features: 18
[LightGBM] [Info] Start training from score -0.805522
[LightGBM] [Info] Start training from score -1.089973
[LightGBM] [Info] Start training from score -1.528228
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes

LGBMClassifier(colsample_bytree=0.8, max_depth=15, n_estimators=50,
               reg_alpha=0.5, reg_lambda=0.5, subsample=0.6)

In [571]:
X_train, y_train = get_train_batch(df_mc_class1, df_mc_class2_train, df_mc_class3_train, 206, 412)

In [572]:
y_train = y_train.map({1: 0, 2: 1, 3: 2})

In [573]:
xgboost2 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost2 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [574]:
random_search.best_params_

{'reg_lambda': 1,
 'reg_alpha': 1e-05,
 'max_depth': 15,
 'learning_rate': 0.01,
 'gamma': 0.3,
 'colsample_bytree': 0.7}

In [575]:
xgboost2 = xgb.XGBClassifier(
reg_lambda = 1,
reg_alpha = 1e-05,
max_depth = 15,
learning_rate = 0.01,
gamma = 0.3,
colsample_bytree = 0.7
)
xgboost2.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.7, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.3, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.01, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=15, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              objective='multi:softprob', predictor=None, ...)

In [576]:
lgb2 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb2 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[CV 4/5] END colsample_bytree=0.4, gamma=0.0, learning_rate=0.0001, max_depth=3, reg_alpha=0.01, reg_lambda=10;, score=0.981 total time=   0.0s
[CV 3/5] END colsample_bytree=0.8, gamma=0.2, learning_rate=0.1, max_depth=12, reg_alpha=1, reg_lambda=1e-05;, score=0.954 total time=   0.0s
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Number of positive: 224, number of negative: 208
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003593 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 707
[LightGBM] [Info] Number of data points in the train

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [577]:
random_search.best_params_

{'subsample': 0.6,
 'reg_lambda': 0.1,
 'reg_alpha': 0.5,
 'num_leaves': 63,
 'n_estimators': 100,
 'min_child_samples': 100,
 'max_depth': 15,
 'learning_rate': 0.1,
 'colsample_bytree': 0.6}

In [578]:
lgb2 = lgb.LGBMClassifier(
subsample = 0.6,
reg_lambda= 0.1,
reg_alpha =0.5,
num_leaves = 63,
n_estimators = 100,
min_child_samples = 100,
max_depth = 15,
learning_rate = 0.1,
colsample_bytree = 0.6
)
lgb2.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000492 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 716
[LightGBM] [Info] Number of data points in the train set: 461, number of used features: 18
[LightGBM] [Info] Start training from score -0.805522
[LightGBM] [Info] Start training from score -1.089973
[LightGBM] [Info] Start training from score -1.528228
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] N

LGBMClassifier(colsample_bytree=0.6, max_depth=15, min_child_samples=100,
               num_leaves=63, reg_alpha=0.5, reg_lambda=0.1, subsample=0.6)

In [579]:
X_train, y_train = get_train_batch(df_mc_class1, df_mc_class2_train, df_mc_class3_train, 412, 618)

In [580]:
y_train = y_train.map({1: 0, 2: 1, 3: 2})

In [581]:
xgboost3 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost3 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [582]:
random_search.best_params_

{'reg_lambda': 100,
 'reg_alpha': 1,
 'max_depth': 6,
 'learning_rate': 1,
 'gamma': 0.1,
 'colsample_bytree': 0.5}

In [583]:
xgboost3 = xgb.XGBClassifier(
reg_lambda = 100,
reg_alpha = 1,
max_depth = 6,
learning_rate = 1,
gamma = 0.1,
colsample_bytree = 0.5
)
xgboost3.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.5, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.1, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=6, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              objective='multi:softprob', predictor=None, ...)

In [584]:
lgb3 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb3,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[CV 2/5] END colsample_bytree=1.0, learning_rate=0.05, max_depth=10, min_child_samples=50, n_estimators=50, num_leaves=31, reg_alpha=0.5, reg_lambda=0.5, subsample=1.0;, score=0.652 total time=   0.9s
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003787 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 678
[LightGBM] [Info] Number of data points in the train set: 369, number of used features: 18
[LightGBM] [Info] Start train

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [585]:
random_search.best_params_

{'subsample': 0.6,
 'reg_lambda': 0.0,
 'reg_alpha': 0.5,
 'num_leaves': 31,
 'n_estimators': 200,
 'min_child_samples': 20,
 'max_depth': 10,
 'learning_rate': 0.05,
 'colsample_bytree': 0.8}

In [586]:
lgb3 = lgb.LGBMClassifier(
subsample = 0.6,
reg_lambda= 0.0,
reg_alpha =0.5,
num_leaves = 31,
n_estimators = 200,
min_child_samples = 20,
max_depth = 10,
learning_rate = 0.05,
colsample_bytree = 0.8
)
lgb3.fit(X_train,y_train)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000492 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 694
[LightGBM] [Info] Number of data points in the train set: 461, number of used features: 18
[LightGBM] [Info] Start training from score -0.805522
[LightGBM] [Info] Start training from score -1.089973
[LightGBM] [Info] Start training from score -1.528228
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes

LGBMClassifier(colsample_bytree=0.8, learning_rate=0.05, max_depth=10,
               n_estimators=200, reg_alpha=0.5, subsample=0.6)

In [587]:
X_train, y_train = get_train_batch(df_mc_class1, df_mc_class2_train, df_mc_class3_train, 618, 824)

In [588]:
y_train = y_train.map({1: 0, 2: 1, 3: 2})

In [589]:
xgboost4 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost4,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [590]:
random_search.best_params_

{'reg_lambda': 0.1,
 'reg_alpha': 1,
 'max_depth': 6,
 'learning_rate': 0.1,
 'gamma': 0.2,
 'colsample_bytree': 0.9}

In [591]:
xgboost4 = xgb.XGBClassifier(
reg_lambda = 0.1,
reg_alpha = 1,
max_depth = 6,
learning_rate = 0.1,
gamma = 0.2,
colsample_bytree = 0.9
)
xgboost4.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.9, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.2, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=6, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              objective='multi:softprob', predictor=None, ...)

In [592]:
lgb4 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb4,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [593]:
random_search.best_params_

{'subsample': 0.6,
 'reg_lambda': 0.5,
 'reg_alpha': 0.1,
 'num_leaves': 31,
 'n_estimators': 200,
 'min_child_samples': 20,
 'max_depth': 10,
 'learning_rate': 0.01,
 'colsample_bytree': 0.8}

In [594]:
lgb4 = lgb.LGBMClassifier(
subsample = 0.6,
reg_lambda= 0.5,
reg_alpha =0.1,
num_leaves = 31,
n_estimators = 200,
min_child_samples = 20,
max_depth = 10,
learning_rate = 0.01,
colsample_bytree = 0.8
)
lgb4.fit(X_train,y_train)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000854 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 712
[LightGBM] [Info] Number of data points in the train set: 461, number of used features: 18
[LightGBM] [Info] Start training from score -0.805522
[LightGBM] [Info] Start training from score -1.089973
[LightGBM] [Info] Start training from score -1.528228
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -in

LGBMClassifier(colsample_bytree=0.8, learning_rate=0.01, max_depth=10,
               n_estimators=200, reg_alpha=0.1, reg_lambda=0.5, subsample=0.6)

In [595]:
X_train, y_train = get_train_batch(df_mc_class1, df_mc_class2_train, df_mc_class3_train, 824, 1030)

In [596]:
y_train = y_train.map({1: 0, 2: 1, 3: 2})

In [597]:
xgboost5 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost5,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [598]:
random_search.best_params_

{'reg_lambda': 0.1,
 'reg_alpha': 1e-05,
 'max_depth': 12,
 'learning_rate': 0.1,
 'gamma': 0.3,
 'colsample_bytree': 0.5}

In [599]:
xgboost5 = xgb.XGBClassifier(
reg_lambda = 0.1,
reg_alpha = 1e-05,
max_depth = 12,
learning_rate = 0.1,
gamma = 0.3,
colsample_bytree = 0.5
)
xgboost5.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.5, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.3, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=12, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              objective='multi:softprob', predictor=None, ...)

In [600]:
lgb5 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb5,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [601]:
random_search.best_params_

{'subsample': 0.6,
 'reg_lambda': 0.5,
 'reg_alpha': 0.1,
 'num_leaves': 15,
 'n_estimators': 100,
 'min_child_samples': 50,
 'max_depth': 10,
 'learning_rate': 0.1,
 'colsample_bytree': 0.8}

In [602]:
lgb5 = lgb.LGBMClassifier(
subsample = 0.6,
reg_lambda= 0.5,
reg_alpha =0.1,
num_leaves = 15,
n_estimators = 100,
min_child_samples = 50,
max_depth = 10,
learning_rate = 0.1,
colsample_bytree = 0.8
)
lgb5.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000336 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 721
[LightGBM] [Info] Number of data points in the train set: 461, number of used features: 18
[LightGBM] [Info] Start training from score -0.805522
[LightGBM] [Info] Start training from score -1.089973
[LightGBM] [Info] Start training from score -1.528228
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] N

LGBMClassifier(colsample_bytree=0.8, max_depth=10, min_child_samples=50,
               num_leaves=15, reg_alpha=0.1, reg_lambda=0.5, subsample=0.6)

In [603]:
X_train, y_train = get_train_batch(df_mc_class1, df_mc_class2_train, df_mc_class3_train, 1030, 1236)

In [604]:
y_train = y_train.map({1: 0, 2: 1, 3: 2})

In [605]:
xgboost6 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost6,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [606]:
random_search.best_params_

{'reg_lambda': 100,
 'reg_alpha': 1,
 'max_depth': 3,
 'learning_rate': 1,
 'gamma': 0.0,
 'colsample_bytree': 0.8}

In [607]:
xgboost6 = xgb.XGBClassifier(
reg_lambda = 100,
reg_alpha = 1,
max_depth = 3,
learning_rate = 1,
gamma = 0.0,
colsample_bytree = 0.8
)
xgboost6.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.8, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.0, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=3, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              objective='multi:softprob', predictor=None, ...)

In [608]:
lgb6 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb6,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [609]:
random_search.best_params_

{'subsample': 1.0,
 'reg_lambda': 0.1,
 'reg_alpha': 0.0,
 'num_leaves': 63,
 'n_estimators': 50,
 'min_child_samples': 50,
 'max_depth': 5,
 'learning_rate': 0.1,
 'colsample_bytree': 1.0}

In [610]:
lgb6 = lgb.LGBMClassifier(
subsample = 1.0,
reg_lambda= 0.1,
reg_alpha =0.0,
num_leaves = 63,
n_estimators = 50,
min_child_samples = 50,
max_depth = 5,
learning_rate = 0.1,
colsample_bytree = 1.0
)
lgb6.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000603 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 710
[LightGBM] [Info] Number of data points in the train set: 461, number of used features: 18
[LightGBM] [Info] Start training from score -0.805522
[LightGBM] [Info] Start training from score -1.089973
[LightGBM] [Info] Start training from score -1.528228
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

LGBMClassifier(max_depth=5, min_child_samples=50, n_estimators=50,
               num_leaves=63, reg_lambda=0.1)

In [611]:
X_train, y_train = get_train_batch(df_mc_class1, df_mc_class2_train, df_mc_class3_train, 1236, 1442)

In [612]:
y_train = y_train.map({1: 0, 2: 1, 3: 2})

In [613]:
xgboost7 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost7,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [614]:
random_search.best_params_

{'reg_lambda': 1,
 'reg_alpha': 0.1,
 'max_depth': 6,
 'learning_rate': 0.1,
 'gamma': 0.4,
 'colsample_bytree': 0.4}

In [615]:
xgboost7 = xgb.XGBClassifier(
reg_lambda = 1,
reg_alpha = 0.1,
max_depth = 6,
learning_rate = 0.1,
gamma = 0.4,
colsample_bytree = 0.4
)
xgboost7.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.4, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.4, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=6, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              objective='multi:softprob', predictor=None, ...)

In [616]:
lgb7 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb7,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [617]:
random_search.best_params_

{'subsample': 0.6,
 'reg_lambda': 0.0,
 'reg_alpha': 0.5,
 'num_leaves': 15,
 'n_estimators': 100,
 'min_child_samples': 20,
 'max_depth': 15,
 'learning_rate': 0.01,
 'colsample_bytree': 0.6}

In [618]:
lgb7 = lgb.LGBMClassifier(
subsample = 0.6,
reg_lambda= 0.0,
reg_alpha =0.5,
num_leaves = 15,
n_estimators = 100,
min_child_samples = 20,
max_depth = 15,
learning_rate = 0.01,
colsample_bytree = 0.6
)
lgb7.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000409 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 705
[LightGBM] [Info] Number of data points in the train set: 461, number of used features: 18
[LightGBM] [Info] Start training from score -0.805522
[LightGBM] [Info] Start training from score -1.089973
[LightGBM] [Info] Start training from score -1.528228
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] N

LGBMClassifier(colsample_bytree=0.6, learning_rate=0.01, max_depth=15,
               num_leaves=15, reg_alpha=0.5, subsample=0.6)

##### Testing set

In [619]:
df_mc_class1_test = df_mc_class1.iloc[1442:]
df_mc_class1_test = df_mc_class1_test.drop(['Unnamed: 0','binary_target'], axis=1)

In [620]:
df_mc_class2_test = df_mc_class2.iloc[155:]
df_mc_class2_test = df_mc_class2_test.drop(['Unnamed: 0','binary_target'], axis=1)

In [621]:
df_mc_class3_test = df_mc_class3.iloc[100:]
df_mc_class3_test = df_mc_class3_test.drop(['Unnamed: 0','binary_target'], axis=1)

In [622]:
def get_test_batch(target1, target2, target3):
    df_test = pd.concat([target1, target2, target3], axis=0)

    X_test = df_test.drop('target', axis=1)
    y_test = df_test.target
    return X_test, y_test

In [623]:
X_test, y_test = get_test_batch(df_mc_class1_test, df_mc_class2_test, df_mc_class3_test)

In [624]:
y_test = y_test.map({1: 0, 2: 1, 3: 2})

In [625]:
y_test

1859    0
1860    0
1861    0
1862    0
1863    0
       ..
2036    2
2037    2
2038    2
2039    2
2048    2
Name: target, Length: 429, dtype: int64

In [626]:
# Creating a list to store models
models = [xgboost1, xgboost2, xgboost3, xgboost4, xgboost5, xgboost6, xgboost7]
results = []

In [627]:
# Creating a list to store models
models_lgb = [lgb1, lgb2, lgb3, lgb4, lgb5, lgb6, lgb7]
results_lgb = []

In [628]:
for model in models:
    y_pred = model.predict(X_test)
    results.append(y_pred)

In [629]:
for model in models_lgb:
    y_pred = model.predict(X_test)
    results_lgb.append(y_pred)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).


In [630]:
import statistics
voted_result = []
# Assuming all lists in the list_of_lists have the same length
for i in range(len(results[0])):
    elements_at_index = [sublist[i] for sublist in results]
    #print(elements_at_index)
    voted_result.append(statistics.mode(elements_at_index))

In [631]:
import statistics
voted_result_lgb = []
# Assuming all lists in the list_of_lists have the same length
for i in range(len(results[0])):
    elements_at_index = [sublist[i] for sublist in results_lgb]
    voted_result_lgb.append(statistics.mode(elements_at_index))

In [632]:
print(accuracy_score(y_test,voted_result)*100)

65.26806526806527


In [633]:
print(accuracy_score(y_test,voted_result_lgb)*100)

62.47086247086248
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightG

### Binary Class

In [5]:
df_bc = pd.read_csv("Dataset_without_outliers_both_class.csv")
df_bc.drop(['Unnamed: 0','target'], axis=1)

baseline value  accelerations  fetal_movement  uterine_contractions  \
0              120.0          0.000           0.000                 0.000   
1              132.0          0.006           0.000                 0.006   
2              133.0          0.003           0.000                 0.008   
3              134.0          0.003           0.000                 0.008   
4              132.0          0.007           0.000                 0.008   
...              ...            ...             ...                   ...   
2121           140.0          0.000           0.000                 0.007   
2122           140.0          0.001           0.000                 0.007   
2123           140.0          0.001           0.000                 0.007   
2124           140.0          0.001           0.000                 0.006   
2125           142.0          0.002           0.002                 0.008   

      light_decelerations  severe_decelerations  prolongued_decelerations  \
0                   0.000                   0.0                       0.0   
1                   0.003                   0.0                       0.0   
2                   0.003                   0.0                       0.0   
3                   0.003                   0.0                       0.0   
4                   0.000                   0.0                       0.0   
...                   ...                   ...                       ...   
2121                0.000                   0.0                       0.0   
2122                0.000                   0.0                       0.0   
2123                0.000                   0.0                       0.0   
2124                0.000                   0.0                       0.0   
2125                0.000                   0.0                       0.0   

      abnormal_short_term_variability  mean_value_of_short_term_variability  \
0                                73.0                                   0.5   
1                                17.0                                   2.1   
2                                16.0                                   2.1   
3                                16.0                                   2.4   
4                                16.0                                   2.4   
...                               ...                                   ...   
2121                             79.0                                   0.2   
2122                             78.0                                   0.4   
2123                             79.0                                   0.4   
2124                             78.0                                   0.4   
2125                             74.0                                   0.4   

      percentage_of_time_with_abnormal_long_term_variability  ...  \
0                                                  27.5       ...   
1                                                   0.0       ...   
2                                                   0.0       ...   
3                                                   0.0       ...   
4                                                   0.0       ...   
...                                                 ...       ...   
2121                                               25.0       ...   
2122                                               22.0       ...   
2123                                               20.0       ...   
2124                                               27.0       ...   
2125                                               27.5       ...   

      histogram_min  histogram_max  histogram_number_of_peaks  \
0              62.0          126.0                        2.0   
1              68.0          198.0                        6.0   
2              68.0          198.0                        5.0   
3              53.0          170.0                       11.0   
4              53.0          170.0                   

In [416]:
df_bc_class1 = df_bc[df_bc.binary_target==1]
df_bc_class2 = df_bc[df_bc.binary_target==0]

In [417]:
df_bc_class1.shape, df_bc_class2.shape

((1655, 24), (471, 24))

In [418]:
df_bc_class2_train = df_bc_class2.iloc[:260]
df_bc_class2_train

Unnamed: 0  baseline value  accelerations  fetal_movement  \
0             0           120.0          0.000          0.0000   
5             5           134.0          0.001          0.0000   
6             6           134.0          0.001          0.0000   
7             7           122.0          0.000          0.0000   
8             8           122.0          0.000          0.0000   
..          ...             ...            ...             ...   
682         682           132.0          0.000          0.0075   
683         683           132.0          0.000          0.0075   
689         689           133.0          0.004          0.0075   
690         690           133.0          0.000          0.0075   
697         697           131.0          0.001          0.0075   

     uterine_contractions  light_decelerations  severe_decelerations  \
0                   0.000               0.0000                   0.0   
5                   0.010               0.0075                   0.0   
6                   0.013               0.0075                   0.0   
7                   0.000               0.0000                   0.0   
8                   0.002               0.0000                   0.0   
..                    ...                  ...                   ...   
682                 0.004               0.0040                   0.0   
683                 0.002               0.0020                   0.0   
689                 0.004               0.0030                   0.0   
690                 0.004               0.0020                   0.0   
697                 0.003               0.0030                   0.0   

     prolongued_decelerations  abnormal_short_term_variability  \
0                         0.0                             73.0   
5                         0.0                             26.0   
6                         0.0                             29.0   
7                         0.0                             83.0   
8                         0.0                             84.0   
..                        ...                              ...   
682                       0.0                             35.0   
683                       0.0                             37.0   
689                       0.0                             21.0   
690                       0.0                             18.0   
697                       0.0                             29.0   

     mean_value_of_short_term_variability  ...  histogram_max  \
0                                     0.5  ...          126.0   
5                                     3.2  ...          200.0   
6                                     3.2  ...          200.0   
7                                     0.5  ...          130.0   
8                                     0.5  ...          130.0   
..                                    ...  ...            ...   
682                                   2.7  ...          199.0   
683                                   2.3  ...          165.0   
689                                   2.3  ...          174.0   
690                                   2.7  ...          174.0   
697                                   2.0  ...          165.0   

     histogram_number_of_peaks  histogram_number_of_zeroes  histogram_mode  \
0                          2.0                         0.0           120.0   
5                          5.0                         0.0           100.5   
6                          6.0                         0.0           100.5   
7                          0.0                         0.0           122.0   
8                          0.0                         0.0           122.0   
..                         ...                         ...             ...   
682                        9.0                         0.0           100.5   
683                        5.0                         0.0           100.5   
689                        7.0                         0.0           14

In [476]:
def get_train_batch(target1, target2, start, end):
    df_train = pd.concat([target1[start:end], target2], axis=0)

    X_train = df_train.drop(['Unnamed: 0','target','binary_target'], axis=1)
    y_train = df_train.binary_target
    return X_train, y_train 

In [477]:
X_train, y_train = get_train_batch(df_bc_class1, df_bc_class2_train, 0, 280)

In [503]:
xgboost1 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost1 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [504]:
random_search.best_params_

{'reg_lambda': 1e-05,
 'reg_alpha': 0.1,
 'max_depth': 12,
 'learning_rate': 0.1,
 'gamma': 0.1,
 'colsample_bytree': 0.9}

In [505]:
xgboost1 = xgb.XGBClassifier(
reg_lambda = 1e-05,
reg_alpha = 0.1,
max_depth = 12,
learning_rate = 0.1,
gamma = 0.1,
colsample_bytree = 0.9
)
xgboost1.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.9, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.1, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=12, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [506]:
lgb1 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb1 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 280, number of negative: 260
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000367 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 770
[LightGBM] [Info] Number of data points in the train set: 540, number of used features: 18
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.518519 -> initscore=0.074108
[LightGBM] [Info] Start training from score 0.074108
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf


RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [507]:
random_search.best_params_

{'subsample': 1.0,
 'reg_lambda': 0.1,
 'reg_alpha': 0.5,
 'num_leaves': 15,
 'n_estimators': 100,
 'min_child_samples': 100,
 'max_depth': 15,
 'learning_rate': 0.1,
 'colsample_bytree': 0.8}

In [508]:
lgb1 = lgb.LGBMClassifier(
subsample = 1.0,
reg_lambda= 0.1,
reg_alpha =0.5,
num_leaves = 15,
n_estimators = 100,
min_child_samples = 100,
max_depth = 15,
learning_rate = 0.1,
colsample_bytree = 0.8
)
lgb1.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 280, number of negative: 260
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000410 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 770
[LightGBM] [Info] Number of data points in the train set: 540, number of used features: 18
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.518519 -> initscore=0.074108
[LightGBM] [Info] Start training from score 0.074108
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

LGBMClassifier(colsample_bytree=0.8, max_depth=15, min_child_samples=100,
               num_leaves=15, reg_alpha=0.5, reg_lambda=0.1)

In [510]:
X_train, y_train = get_train_batch(df_bc_class1, df_bc_class2_train, 280, 560)

In [511]:
xgboost2 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost2 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [512]:
random_search.best_params_

{'reg_lambda': 1,
 'reg_alpha': 1,
 'max_depth': 15,
 'learning_rate': 0.1,
 'gamma': 0.3,
 'colsample_bytree': 0.7}

In [513]:
xgboost2 = xgb.XGBClassifier(
reg_lambda = 1,
reg_alpha = 1,
max_depth = 15,
learning_rate = 0.1,
gamma = 0.3,
colsample_bytree = 0.7
)
xgboost2.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.7, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.3, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=15, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [514]:
lgb2 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb2 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Number of positive: 280, number of negative: 260
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000319 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 743
[LightGBM] [Info] Number of data points in the train set: 540, number of used features: 18
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.518519 -> initscore=0.074108
[LightGBM] [Info] Start training from score 0.074108
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [515]:
random_search.best_params_

{'subsample': 1.0,
 'reg_lambda': 0.1,
 'reg_alpha': 0.5,
 'num_leaves': 31,
 'n_estimators': 200,
 'min_child_samples': 20,
 'max_depth': 5,
 'learning_rate': 0.05,
 'colsample_bytree': 0.8}

In [516]:
lgb2 = lgb.LGBMClassifier(
subsample = 1.0,
reg_lambda= 0.1,
reg_alpha =0.5,
num_leaves = 31,
n_estimators = 200,
min_child_samples = 20,
max_depth = 5,
learning_rate = 0.01,
colsample_bytree = 0.8
)
lgb2.fit(X_train,y_train)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Number of positive: 280, number of negative: 260
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000336 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 743
[LightGBM] [Info] Number of data points in the train set: 540, number of used features: 18
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.518519 -> initscore=0.074108
[LightGBM] [Info] Start training from score 0.074108
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

LGBMClassifier(colsample_bytree=0.8, learning_rate=0.01, max_depth=5,
               n_estimators=200, reg_alpha=0.5, reg_lambda=0.1)

In [517]:
X_train, y_train = get_train_batch(df_bc_class1, df_bc_class2_train, 560, 840)

In [518]:
xgboost3 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost3 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [519]:
random_search.best_params_

{'reg_lambda': 0.01,
 'reg_alpha': 10,
 'max_depth': 15,
 'learning_rate': 1,
 'gamma': 0.1,
 'colsample_bytree': 0.8}

In [520]:
xgboost3 = xgb.XGBClassifier(
reg_lambda = 0.01,
reg_alpha = 10,
max_depth = 15,
learning_rate = 1,
gamma = 0.1,
colsample_bytree = 0.8
)
xgboost3.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.8, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.1, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=15, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [521]:
lgb3 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb3 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[CV 1/5] END colsample_bytree=0.9, gamma=0.1, learning_rate=0.1, max_depth=12, reg_alpha=0.1, reg_lambda=1e-05;, score=0.861 total time=   0.1s
[CV 4/5] END colsample_bytree=0.9, gamma=0.4, learning_rate=0.01, max_depth=15, reg_alpha=100, reg_lambda=10;, score=0.481 total time=   0.0s
[CV 3/5] END colsample_bytree=0.3, gamma=0.4, learning_rate=0.01, max_depth=6, reg_alpha=10, reg_lambda=1;, score=0.963 total time=   0.0s
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Number of positive: 224, number of negative: 208
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003717 seconds.
You 

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [522]:
random_search.best_params_

{'subsample': 0.8,
 'reg_lambda': 0.5,
 'reg_alpha': 0.5,
 'num_leaves': 15,
 'n_estimators': 100,
 'min_child_samples': 20,
 'max_depth': 10,
 'learning_rate': 0.1,
 'colsample_bytree': 0.6}

In [523]:
lgb3 = lgb.LGBMClassifier(
subsample = 0.8,
reg_lambda= 0.5,
reg_alpha =0.5,
num_leaves = 15,
n_estimators = 100,
min_child_samples = 20,
max_depth = 10,
learning_rate = 0.1,
colsample_bytree = 0.6
)
lgb3.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 280, number of negative: 260
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000504 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 745
[LightGBM] [Info] Number of data points in the train set: 540, number of used features: 18
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.518519 -> initscore=0.074108
[LightGBM] [Info] Start training from score 0.074108
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

LGBMClassifier(colsample_bytree=0.6, max_depth=10, num_leaves=15, reg_alpha=0.5,
               reg_lambda=0.5, subsample=0.8)

In [524]:
X_train, y_train = get_train_batch(df_bc_class1, df_bc_class2_train, 840, 1120)

In [525]:
xgboost4 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost4 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [526]:
random_search.best_params_

{'reg_lambda': 1,
 'reg_alpha': 1e-05,
 'max_depth': 3,
 'learning_rate': 0.1,
 'gamma': 0.0,
 'colsample_bytree': 0.7}

In [527]:
xgboost4 = xgb.XGBClassifier(
reg_lambda = 1,
reg_alpha = 1e-05,
max_depth = 3,
learning_rate = 0.1,
gamma = 0.0,
colsample_bytree = 0.7
)
xgboost4.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.7, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.0, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=3, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [528]:
lgb4 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb4 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[CV 1/5] END colsample_bytree=0.8, gamma=0.3, learning_rate=1, max_depth=6, reg_alpha=0.1, reg_lambda=1;, score=0.843 total time=   0.0s
[CV 2/5] END colsample_bytree=0.9, gamma=0.4, learning_rate=0.01, max_depth=15, reg_alpha=100, reg_lambda=10;, score=0.481 total time=   0.0s
[CV 2/5] END colsample_bytree=0.3, gamma=0.4, learning_rate=0.01, max_depth=6, reg_alpha=10, reg_lambda=1;, score=0.954 total time=   0.0s
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Number of positive: 224, number of negative: 208
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003930 seconds.
You can set

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [529]:
random_search.best_params_

{'subsample': 1.0,
 'reg_lambda': 0.5,
 'reg_alpha': 0.1,
 'num_leaves': 63,
 'n_estimators': 100,
 'min_child_samples': 50,
 'max_depth': 15,
 'learning_rate': 0.01,
 'colsample_bytree': 1.0}

In [530]:
lgb4 = lgb.LGBMClassifier(
subsample = 1.0,
reg_lambda= 0.5,
reg_alpha =0.1,
num_leaves = 63,
n_estimators = 100,
min_child_samples = 50,
max_depth = 15,
learning_rate = 0.01,
colsample_bytree = 1.0
)
lgb4.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 280, number of negative: 260
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000570 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 540, number of used features: 18
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.518519 -> initscore=0.074108
[LightGBM] [Info] Start training from score 0.074108
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -

LGBMClassifier(learning_rate=0.01, max_depth=15, min_child_samples=50,
               num_leaves=63, reg_alpha=0.1, reg_lambda=0.5)

In [531]:
X_train, y_train = get_train_batch(df_bc_class1, df_bc_class2_train, 1120, 1400)

In [532]:
xgboost5 = xgb.XGBClassifier()

# hyperparameter tuning
param_grid = {
    "learning_rate": [0.0001,0.001, 0.01, 0.1, 1] ,
    "max_depth": range(3,21,3),
    "gamma": [i/10.0 for i in range(0,5)],
    "colsample_bytree": [i/10.0 for i in range(3,10)],
    "reg_alpha": [1e-5, 1e-2, 0.1, 1, 10, 100],
    "reg_lambda": [1e-5, 1e-2, 0.1, 1, 10, 100]}

random_search=RandomizedSearchCV(xgboost5,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/muntaqimahmedraju/miniforge3/envs/pythonhub/lib/python3.9/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a f

RandomizedSearchCV(cv=5,
                   estimator=XGBClassifier(base_score=None, booster=None,
                                           callbacks=None,
                                           colsample_bylevel=None,
                                           colsample_bynode=None,
                                           colsample_bytree=None,
                                           early_stopping_rounds=None,
                                           enable_categorical=False,
                                           eval_metric=None, feature_types=None,
                                           gamma=None, gpu_id=None,
                                           grow_policy=None,
                                           importance_type=None,
                                           interaction_constraints=None,
                                           learning_rate...
                                           num_parallel_tree=None,
                                           predictor=None, random_state=None, ...),
                   n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.3, 0.4, 0.5, 0.6,
                                                             0.7, 0.8, 0.9],
                                        'gamma': [0.0, 0.1, 0.2, 0.3, 0.4],
                                        'learning_rate': [0.0001, 0.001, 0.01,
                                                          0.1, 1],
                                        'max_depth': range(3, 21, 3),
                                        'reg_alpha': [1e-05, 0.01, 0.1, 1, 10,
                                                      100],
                                        'reg_lambda': [1e-05, 0.01, 0.1, 1, 10,
                                                       100]},
                   scoring='accuracy', verbose=3)

In [533]:
random_search.best_params_

{'reg_lambda': 0.01,
 'reg_alpha': 10,
 'max_depth': 15,
 'learning_rate': 0.1,
 'gamma': 0.2,
 'colsample_bytree': 0.3}

In [534]:
xgboost5 = xgb.XGBClassifier(
reg_lambda = 0.01,
reg_alpha = 10,
max_depth = 15,
learning_rate = 0.1,
gamma = 0.2,
colsample_bytree = 0.3
)
xgboost5.fit(X_train,y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.3, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=0.2, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.1, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=15, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [535]:
lgb5 = lgb.LGBMClassifier()

param_grid = {
    'learning_rate': [0.01, 0.05, 0.1],  # Learning rate (shrinkage)
    'n_estimators': [50, 100, 200],  # Number of boosting iterations
    'num_leaves': [15, 31, 63],  # Maximum number of leaves in a tree
    'max_depth': [5, 10, 15],  # Maximum tree depth for depth-wise tree growth
    'subsample': [0.6, 0.8, 1.0],  # Subsample ratio of the training instance
    'colsample_bytree': [0.6, 0.8, 1.0],  # Subsample ratio of columns when constructing each tree
    'min_child_samples': [20, 50, 100],  # Minimum number of data needed in a leaf
    'reg_alpha': [0.0, 0.1, 0.5],  # L1 regularization term on weights
    'reg_lambda': [0.0, 0.1, 0.5],  # L2 regularization term on weights
}
random_search=RandomizedSearchCV(lgb5 ,param_distributions=param_grid,n_iter=5,scoring='accuracy',n_jobs=-1,cv=5,verbose=3)
random_search.fit(X_train,y_train)

Fitting 5 folds for each of 5 candidates, totalling 25 fits
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(), n_iter=5, n_jobs=-1,
                   param_distributions={'colsample_bytree': [0.6, 0.8, 1.0],
                                        'learning_rate': [0.01, 0.05, 0.1],
                                        'max_depth': [5, 10, 15],
                                        'min_child_samples': [20, 50, 100],
                                        'n_estimators': [50, 100, 200],
                                        'num_leaves': [15, 31, 63],
                                        'reg_alpha': [0.0, 0.1, 0.5],
                                        'reg_lambda': [0.0, 0.1, 0.5],
                                        'subsample': [0.6, 0.8, 1.0]},
                   scoring='accuracy', verbose=3)

In [536]:
random_search.best_params_

{'subsample': 0.6,
 'reg_lambda': 0.5,
 'reg_alpha': 0.1,
 'num_leaves': 15,
 'n_estimators': 200,
 'min_child_samples': 50,
 'max_depth': 5,
 'learning_rate': 0.1,
 'colsample_bytree': 0.8}

In [537]:
lgb5 = lgb.LGBMClassifier(
subsample = 0.6,
reg_lambda= 0.5,
reg_alpha =0.1,
num_leaves = 15,
n_estimators = 200,
min_child_samples = 50,
max_depth = 5,
learning_rate = 0.1,
colsample_bytree = 0.8
)
lgb5.fit(X_train,y_train)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 280, number of negative: 260
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000593 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 770
[LightGBM] [Info] Number of data points in the train set: 540, number of used features: 18
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.518519 -> initscore=0.074108
[LightGBM] [Info] Start training from score 0.074108
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

LGBMClassifier(colsample_bytree=0.8, max_depth=5, min_child_samples=50,
               n_estimators=200, num_leaves=15, reg_alpha=0.1, reg_lambda=0.5,
               subsample=0.6)

### Testing Set

In [538]:
df_bc_class1_test = df_bc_class1.iloc[1400:]
df_bc_class1_test = df_bc_class1_test.drop(['Unnamed: 0','target'], axis=1)

In [539]:
df_bc_class2_test = df_bc_class2.iloc[260:]
df_bc_class2_test = df_bc_class2_test.drop(['Unnamed: 0','target'], axis=1)

In [540]:
def get_test_batch(target1, target2):
    df_test = pd.concat([target1, target2], axis=0)

    X_test = df_test.drop('binary_target', axis=1)
    y_test = df_test.binary_target
    return X_test, y_test

In [541]:
X_test, y_test = get_test_batch(df_bc_class1_test, df_bc_class2_test)

In [542]:
# Creating a list to store models
models = [xgboost1, xgboost2, xgboost3, xgboost4, xgboost5]
results = []

In [543]:
for model in models:
    y_pred = model.predict(X_test)
    results.append(y_pred)

In [544]:
import statistics
voted_result = []
# Assuming all lists in the list_of_lists have the same length
for i in range(len(results[0])):
    elements_at_index = [sublist[i] for sublist in results]
    #print(elements_at_index)
    voted_result.append(statistics.mode(elements_at_index))

In [545]:
print(accuracy_score(y_test,voted_result)*100)

67.81115879828327


In [546]:
# Creating a list to store models
models_lgb = [lgb1, lgb2, lgb3, lgb4, lgb5]
results_lgb = []

In [547]:
for model in models_lgb:
    y_pred = model.predict(X_test)
    results_lgb.append(y_pred)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).


In [550]:
import statistics
voted_result_lgb = []
# Assuming all lists in the list_of_lists have the same length
for i in range(len(results_lgb[0])):
    elements_at_index = [sublist[i] for sublist in results_lgb]
    voted_result_lgb.append(statistics.mode(elements_at_index))

In [551]:
print(accuracy_score(y_test,voted_result_lgb)*100)

64.8068669527897
